In [1]:
import pandas as pd
import numpy as np
import re
import dask.dataframe as dd
import pyarrow.parquet as pq
from pyspark.sql import SparkSession

spark = SparkSession \
    .builder \
    .appName('Python Spark SQL basic example') \
    .config('spark.some.config.option', 'some-value') \
    .getOrCreate()

pd.set_option('display.max_columns', 40)
pd.set_option('display.max_rows', 5000)


In [2]:
def read_and_reduce_columns_USDA_census_parquet(usda_ag_census_input_parquet):
    """
    takes a parquet of one years USDA census of Agriculture data
    selects crops (ignores animals, economics/sales, etc)
    removes redundant, semi-redundant and just plain confusing data
    for more info see the README file at https://github.com/Rafael-SV/ag_census_analysis
    """
    initial_columns_to_select = 'DOMAIN_DESC,SECTOR_DESC,PRODN_PRACTICE_DESC,CLASS_DESC,COMMODITY_DESC,SHORT_DESC,UNIT_DESC,\
    VALUE,YEAR,COUNTY_NAME,STATE_FIPS_CODE,COUNTY_CODE,ASD_DESC,STATE_ALPHA,STATISTICCAT_DESC'
    dataframe_new = spark.read.parquet(usda_ag_census_input_parquet)
    dataframe_new.createOrReplaceTempView('dataframe_new')
    less_columns_df = spark.sql("SELECT {} FROM dataframe_new".format(initial_columns_to_select))
    less_columns_df.createOrReplaceTempView('less_columns_df')
    return less_columns_df
    
def reduce_statisticcat_redundancies(spark_usda_ag_census_sans_df_suffix):
    """
    STATISTICCAT_DESC has a lot of redundant or not useful values in it, so we chop these
    NOTE this function takes as argument the dataframe name WITHOUT the '_df' at the end
    becuase if the entire dataframe name is called as a string formating parameter
    the entire dataframe gets stuffed into the string, causing errors. spark.sql takes a
    string as parameter so we need to do a little gymnastics
    """
    filtered_statisticcat_dataframe = spark.sql("""
    SELECT * 
      FROM {}_df 
     WHERE STATISTICCAT_DESC = 'AREA HARVESTED'
        OR STATISTICCAT_DESC = 'AREA NOT HARVESTED'
        OR STATISTICCAT_DESC = 'AREA IN PRODUCTION'
        OR STATISTICCAT_DESC = 'AREA BEARING'
        OR STATISTICCAT_DESC = 'AREA NON-BEARING'
        OR STATISTICCAT_DESC = 'AREA GROWN'
    """.format(spark_usda_ag_census_sans_df_suffix))
    filtered_statisticcat_dataframe.createOrReplaceTempView("filtered_statisticcat_dataframe")
    return filtered_statisticcat_dataframe


def remove_hay_and_haylage_desc(spark_usda_ag_census_sans_df_suffix):
    """
    remove some commodity types that are redundant, (hopefully) unimportant or otherwise confusing
    NOTE: this function takes as argument the dataframe name WITHOUT the '_df' suffix, reasoning given
    in another functions in this notebook and in 'https://rafaelscode.wordpress.com/'
    """
    filtered_commodity_dataframe = spark.sql("""
    SELECT *
      FROM {}_df
     WHERE COMMODITY_DESC NOT LIKE 'HAY'
       AND COMMODITY_DESC NOT LIKE 'HAYLAGE'
       AND COMMODITY_DESC NOT LIKE '%TOTALS'
       AND COMMODITY_DESC NOT LIKE 'GRAIN STORAGE CAPACITY'
    """.format(spark_usda_ag_census_sans_df_suffix))
    filtered_commodity_dataframe.createOrReplaceTempView("filtered_commodity_dataframe")
    return filtered_commodity_dataframe

def remove_units(spark_usda_ag_census_sans_df_suffix):
    """
    keep only rows with units of area, or number of operations
    NOTE: this function takes as argument the dataframe name WITHOUT the '_df' suffix, reasoning given
    in another functions in this notebook and in 'https://rafaelscode.wordpress.com/'
    """
    filtered_unit_and_production_dataframe = spark.sql("""
        SELECT *
          FROM {}_df
         WHERE
              (UNIT_DESC LIKE 'OPERATIONS'
              OR UNIT_DESC LIKE 'SQ FT'
              OR UNIT_DESC LIKE 'ACRES')
          AND PRODN_PRACTICE_DESC = 'ALL PRODUCTION PRACTICES'
          AND DOMAIN_DESC = 'TOTAL'
    """.format(spark_usda_ag_census_sans_df_suffix))
    filtered_unit_and_production_dataframe.createOrReplaceTempView("filtered_unit_and_production_dataframe")
    return filtered_unit_and_production_dataframe

def remove_redundant_commodity_desc(spark_usda_ag_census_sans_df_suffix):
    """
    some commodities have multiple CLASS_DESC, some have CLASS_DESC='ALL CLASSES', some do not.
    But there are commodities with multiple CLASS_DESC and no aggregate 'ALL CLASSES' and some that do.
    Most commodities with only one CLASS_DESC have it as 'ALL CLASSES',
    yet a few have one CLASS_DESC and it is specific ie blackberries.CLASS_DESC = 'INCL DEWBERRIES & MARIONBERRIES'
    This function filters out the reduntant 'ALL CLASSES' if there are other categories to use instead 
    then UNION the result with the rows that have only 1 CLASS_DESC
    NOTE: this function takes as argument the dataframe name WITHOUT the '_df' suffix, reasoning given
    in another functions in this notebook and in 'https://rafaelscode.wordpress.com/'
    """
    query = """
    SELECT *
      FROM 
           (SELECT *
              FROM {0}_df
             WHERE CLASS_DESC != 'ALL CLASSES'
               AND COMMODITY_DESC IN
                    (SELECT COMMODITY_DESC
                       FROM {0}_df
                   GROUP BY COMMODITY_DESC
                     HAVING COUNT(DISTINCT CLASS_DESC) > 1))
     UNION
            (SELECT *
            FROM {0}_df
            WHERE COMMODITY_DESC IN
                (SELECT COMMODITY_DESC FROM {0}_df
                GROUP BY COMMODITY_DESC
                HAVING COUNT(DISTINCT CLASS_DESC) = 1))
    ORDER BY STATE_ALPHA, COUNTY_NAME
    """.format(spark_usda_ag_census_sans_df_suffix)
    #print(query)
    less_commodity_desc_df = spark.sql(query)
    less_commodity_desc_df.createOrReplaceTempView("less_commodity_desc_df")
    return less_commodity_desc_df
    #print("test")

def remove_rows_w_no_county(spark_usda_ag_census_sans_df_suffix):
    """
    keep only rows with county name present
    NOTE: this function takes as argument the dataframe name WITHOUT the '_df' suffix, reasoning given
    in another functions in this notebook and in 'https://rafaelscode.wordpress.com/'
    """
    with_county_name_df = spark.sql("""
        SELECT *
          FROM {}_df
         WHERE COUNTY_NAME !='None'
    """.format(spark_usda_ag_census_sans_df_suffix))
    with_county_name_df.createOrReplaceTempView("with_county_name_df")
    return with_county_name_df

def remove_more_columns(spark_usda_ag_census_sans_df_suffix):
    """
    earlier functions kept only 1 value for each of DOMAIN_DESC, SECTOR_DESC and PRODN_PRACTICES 
    so we can get rid of these columns now
    NOTE: this function takes as argument the dataframe name WITHOUT the '_df' suffix, reasoning given
    in another functions in this notebook and in 'https://rafaelscode.wordpress.com/'
    """
    final_columns_to_select = 'CLASS_DESC,COMMODITY_DESC,SHORT_DESC,UNIT_DESC,\
    VALUE,YEAR,STATE_ALPHA,COUNTY_NAME,ASD_DESC,STATISTICCAT_DESC'    
    query = "SELECT {0} FROM {1}_df".format(final_columns_to_select, spark_usda_ag_census_sans_df_suffix)
    less_columns_df = spark.sql(query)
    less_columns_df.createOrReplaceTempView("less_columns_df")
    return less_columns_df

    
def invoke_usda_ag_census_dataframe_cleaning_functions(usda_ag_census_name):    
    census_df = read_and_reduce_columns_USDA_census_parquet("./{}.parquet".format(usda_ag_census_name))
    census_df.createOrReplaceTempView("census_df")

    less_statisticcat_df = reduce_statisticcat_redundancies("census")
    less_statisticcat_df.createOrReplaceTempView("less_statisticcat_df")

    less_statisticat_and_commodity_df = remove_hay_and_haylage_desc("less_statisticcat")
    less_statisticat_and_commodity_df.createOrReplaceTempView("less_statisticat_and_commodity_df")

    less_statisticat_and_commodity_and_units_df = remove_units("less_statisticat_and_commodity")
    less_statisticat_and_commodity_and_units_df.createOrReplaceTempView(
        "less_statisticat_and_commodity_and_units_df")

    with_county_name_less_statisticat_and_commodity_and_units_df = remove_rows_w_no_county(
        "less_statisticat_and_commodity_and_units")
    with_county_name_less_statisticat_and_commodity_and_units_df.createOrReplaceTempView(
        "with_county_name_less_statisticat_and_commodity_and_units_df")

    less_commodity_with_county_name_less_statisticat_and_commodity_and_units_df = remove_redundant_commodity_desc(
        "with_county_name_less_statisticat_and_commodity_and_units")
    less_commodity_with_county_name_less_statisticat_and_commodity_and_units_df.createOrReplaceTempView(
        "less_commodity_with_county_name_less_statisticat_and_commodity_and_units_df")    
    
    fully_cleaned_df = remove_more_columns(
        "less_commodity_with_county_name_less_statisticat_and_commodity_and_units")
    fully_cleaned_df.createOrReplaceTempView("fully_cleaned_df")
    return fully_cleaned_df

In [3]:
cleaned_2002_df = invoke_usda_ag_census_dataframe_cleaning_functions('census_02')
print('cleaned_2002_df row count =', cleaned_2002_df.count())
try:
    cleaned_2002_df.write.parquet("./cleaned_2002.parquet")
except:
    print('Parquet already exists, new one not written')
    
cleaned_2007_df = invoke_usda_ag_census_dataframe_cleaning_functions('census_07')
print('cleaned_2007_df row count =', cleaned_2007_df.count())
try:
    cleaned_2007_df.write.parquet("./cleaned_2007.parquet")
except:
    print('Parquet already exists, new one not written')
    
cleaned_2012_df = invoke_usda_ag_census_dataframe_cleaning_functions('census_12')
print('cleaned_2012_df row count =', cleaned_2012_df.count())
try:
    cleaned_2012_df.write.parquet("./cleaned_2012.parquet")
except:
    print('Parquet already exists, new one not written')

cleaned_2002_df row count = 196638
cleaned_2007_df row count = 308915
cleaned_2012_df row count = 324836


In [4]:
cleaned_truncated_df = invoke_usda_ag_census_dataframe_cleaning_functions('census_truncated')
print('cleaned_truncated_df row count =', cleaned_truncated_df.count())
try:
    cleaned_truncated_df.write.parquet("./cleaned_truncated_df.parquet")
except:
    print('Parquet already exists')

cleaned_truncated_df row count = 111


In [21]:
cleaned_truncated_df.show(5)

+--------------------+------------------+--------------------+----------+-----+----+-----------+---------------+-----------+-----------+---------------+-----------------+
|          CLASS_DESC|    COMMODITY_DESC|          SHORT_DESC| UNIT_DESC|VALUE|YEAR|STATE_ALPHA|STATE_FIPS_CODE|COUNTY_NAME|COUNTY_CODE|       ASD_DESC|STATISTICCAT_DESC|
+--------------------+------------------+--------------------+----------+-----+----+-----------+---------------+-----------+-----------+---------------+-----------------+
|         ALL CLASSES|               SOD|SOD - OPERATIONS ...|OPERATIONS|    4|2002|         AL|              1|    COLBERT|         33|NORTHERN VALLEY|   AREA HARVESTED|
|GREEN, SOUTHERN (...|              PEAS|PEAS, GREEN, SOUT...|OPERATIONS|    2|2002|         AL|              1|    COLBERT|         33|NORTHERN VALLEY|   AREA HARVESTED|
|GREEN, SOUTHERN (...|              PEAS|PEAS, GREEN, SOUT...|     ACRES|  (D)|2002|         AL|              1|    COLBERT|         33|NORTHERN 

In [25]:
cleaned_2002_df.createOrReplaceTempView("cleaned_2002_df")
check_distinct_statisticcat_df = spark.sql("SELECT DISTINCT STATISTICCAT_DESC FROM cleaned_2002_df")
cleaned_2002_df.createOrReplaceTempView("cleaned_2002_df")
cleaned_2002_df.limit(1000).toPandas().tail(1000)

CLASS_DESC                       COMMODITY_DESC  \
0                        ALL CLASSES               SHORT TERM WOODY CROPS   
1                        ALL CLASSES                        HAY & HAYLAGE   
2                               HEAD                              CABBAGE   
3                        ALL CLASSES  CUT FLOWERS & CUT CULTIVATED GREENS   
4                        ALL CLASSES                                 OATS   
5                        ALL CLASSES                             POTATOES   
6                        ALL CLASSES                             BROCCOLI   
7                        ALL CLASSES                               BARLEY   
8                        ALL CLASSES                          CAULIFLOWER   
9                               LEAF                              LETTUCE   
10                       ALL CLASSES                              RHUBARB   
11                       ALL CLASSES                          CAULIFLOWER   
12                       ALL CLASSES                              CARROTS   
13                              LEAF                              LETTUCE   
14                       ALL CLASSES                       BERRIES, OTHER   
15                       ALL CLASSES                       BERRIES, OTHER   
16                       ALL CLASSES                              CARROTS   
17                       ALL CLASSES               SHORT TERM WOODY CROPS   
18                              HEAD                              CABBAGE   
19                       ALL CLASSES                                 OATS   
20                       ALL CLASSES                              RHUBARB   
21                       ALL CLASSES                        HAY & HAYLAGE   
22                       ALL CLASSES                             BROCCOLI   
23                       ALL CLASSES                             POTATOES   
24                       ALL CLASSES                               BARLEY   
25                       ALL CLASSES               SHORT TERM WOODY CROPS   
26                              SNAP                                BEANS   
27                              HEAD                              CABBAGE   
28                       ALL CLASSES                              TURNIPS   
29                       ALL CLASSES                                  SOD   
30                       ALL CLASSES             FRUIT & TREE NUTS, OTHER   
31                               DRY    BULBS & CORMS & RHIZOMES & TUBERS   
32                       ALL CLASSES                     BRUSSELS SPROUTS   
33                            TURNIP                               GREENS   
34                               DRY                                HERBS   
35                       ALL CLASSES                              CARROTS   
36                       ALL CLASSES                                 OATS   
37                       ALL CLASSES                               SQUASH   
38                       ALL CLASSES                               APPLES   
39                       ALL CLASSES                             BROCCOLI   
40                       ALL CLASSES                    VEGETABLES, MIXED   
41                              HEAD                              CABBAGE   
42                       ALL CLASSES                               CELERY   
43                       ALL CLASSES                                  SOD   
44                           ROMAINE                              LETTUCE   
45                       ALL CLASSES                       BERRIES, OTHER   
46                       ALL CLASSES                       BERRIES, OTHER   
47                       ALL CLASSES                          CAULIFLOWER   
48                              HEAD                              LETTUCE   
49                       ALL CLASSES                             BROCCOLI   
50                              KALE                               GREENS   
51            GREEN, (

In [3]:
# error checking cell
cleaned_2002_df = invoke_usda_ag_census_dataframe_cleaning_functions('census_02')


In [5]:
# error checking cell
cleaned_2002_df.createOrReplaceTempView("cleaned_2002_df")
check_county_names_df = spark.sql("""
    SELECT * 
    FROM cleaned_2002_df 
    WHERE VALUE = '(Z)' 
""")
check_county_names_df.createOrReplaceTempView("check_county_names_df")
check_county_names_df.limit(1000).toPandas().head(1000)

CLASS_DESC            COMMODITY_DESC  \
0                               HEAD                   LETTUCE   
1                        ALL CLASSES                  RADISHES   
2                        ALL CLASSES            PLUMS & PRUNES   
3                        ALL CLASSES                      FIGS   
4                            COLLARD                    GREENS   
5                              CHILE                   PEPPERS   
6                               TAME               BLUEBERRIES   
7                        ALL CLASSES                 CUCUMBERS   
8                        ALL CLASSES                    GARLIC   
9                        ALL CLASSES                 ASPARAGUS   
10                       ALL CLASSES                  BROCCOLI   
11                       ALL CLASSES                    GRAPES   
12                       ALL CLASSES            PLUMS & PRUNES   
13                       ALL CLASSES                    APPLES   
14                       ALL CLASSES                NECTARINES   
15                       ALL CLASSES                SWEET CORN   
16                       ALL CLASSES                  EGGPLANT   
17                       ALL CLASSES                 ASPARAGUS   
18                       ALL CLASSES                  APRICOTS   
19                       ALL CLASSES            PLUMS & PRUNES   
20                       ALL CLASSES                     PLUMS   
21                       ALL CLASSES                PERSIMMONS   
22                       ALL CLASSES              POMEGRANATES   
23                       ALL CLASSES              STRAWBERRIES   
24                             SWEET                  CHERRIES   
25                       ALL CLASSES                NECTARINES   
26                        WATERMELON                    MELONS   
27                       ALL CLASSES                     LIMES   
28                       ALL CLASSES                   ALMONDS   
29                           ROMAINE                   LETTUCE   
30                       MID & NAVEL                   ORANGES   
31                       ALL CLASSES                TANGERINES   
32                       ALL CLASSES                GRAPEFRUIT   
33                       ALL CLASSES          TREE NUTS, OTHER   
34                       ALL CLASSES                  APRICOTS   
35                       ALL CLASSES                    GARLIC   
36                               DRY                    ONIONS   
37                       ALL CLASSES                  RADISHES   
38                       ALL CLASSES                   TURNIPS   
39                       ALL CLASSES                PERSIMMONS   
40                             SWEET                  CHERRIES   
41                       ALL CLASSES                 HAZELNUTS   
42                       ALL CLASSES                    CELERY   
43                       ALL CLASSES                 HAZELNUTS   
44                       ALL CLASSES               CAULIFLOWER   
45                       ALL CLASSES                    SQUASH   
46                       ALL CLASSES                 CUCUMBERS   
47                              SNAP                     BEANS   
48                       ALL CLASSES                 CUCUMBERS   
49                              SNAP                     BEANS   
50                              KALE                    GREENS   
51                       ALL CLASSES                  TANGELOS   
52                       ALL CLASSES         VEGETABLES, OTHER   
53                       ALL CLASSES                      FIGS   
54                             CHILE                   PEPPERS   
55                       ALL CLASSES            BERRIES, OTHER   
56                       ALL CLASSES                  PUMPKINS   
57                       ALL CLASSES                NECTARINES   
58                       ALL CLASSES                ARTICHOKES   
59                       ALL CLASSES                PERSIMMONS   


In [17]:
check_county_names_df = spark.sql("""
    SELECT DISTINCT COUNTY_NAME, COUNTY_CODE 
    FROM fully_cleaned_2002_df 
    WHERE STATE_ALPHA = 'AK' 
""")
check_county_names_df.createOrReplaceTempView("check_county_names_df")
check_county_names_df.limit(1000).toPandas().tail(1000)


COUNTY_NAME  COUNTY_CODE
0                JUNEAU        110.0
1       KENAI PENINSULA        122.0
2                  None          NaN
3      ALEUTIAN ISLANDS         10.0
4  FAIRBANKS NORTH STAR         90.0
5             ANCHORAGE         20.0

In [5]:
test_df = pd.read_excel("./LND01.xls")
test_df_renamed = test_df.rename(index=str, columns={'LND010190D':'square_miles'})
#test_df_renamed['COUNTY_NAME'], test_df_renamed['STATE_ALPHA'] = \
shorter_test_df = test_df_renamed[['Areaname', 'square_miles', 'STCOU']].copy()
shorter_test_df.Areaname = shorter_test_df.Areaname.str.upper()
#shorter_test_df.head(500)

In [6]:
fully_cleaned_2002_df.write.parquet("./fully_cleaned_2002.parquet")

AnalysisException: 'path file:/home/spazzmo1EE6/ag_census_analysis/fully_cleaned_2002.parquet already exists.;'

AnalysisException: 'Detected implicit cartesian product for LEFT OUTER join between logical plans\nLocalLimit 500\n+- Sort [STATE_ALPHA#294 ASC NULLS FIRST, COUNTY_NAME#300 ASC NULLS FIRST], true\n   +- Aggregate [DOMAIN_DESC#289, SECTOR_DESC#280, PRODN_PRACTICE_DESC#284, CLASS_DESC#283, COMMODITY_DESC#282, SHORT_DESC#288, UNIT_DESC#287, VALUE#316, YEAR#309, COUNTY_NAME#300, COUNTY_CODE#299, ASD_DESC#297, STATE_ALPHA#294, STATISTICCAT_DESC#286], [DOMAIN_DESC#289, SECTOR_DESC#280, PRODN_PRACTICE_DESC#284, CLASS_DESC#283, COMMODITY_DESC#282, SHORT_DESC#288, UNIT_DESC#287, VALUE#316, YEAR#309, COUNTY_NAME#300, COUNTY_CODE#299, ASD_DESC#297, STATE_ALPHA#294, STATISTICCAT_DESC#286]\n      +- Union\n         :- Project [DOMAIN_DESC#289, SECTOR_DESC#280, PRODN_PRACTICE_DESC#284, CLASS_DESC#283, COMMODITY_DESC#282, SHORT_DESC#288, UNIT_DESC#287, VALUE#316, YEAR#309, COUNTY_NAME#300, COUNTY_CODE#299, ASD_DESC#297, STATE_ALPHA#294, STATISTICCAT_DESC#286]\n         :  +- Filter ((((isnotnull(CLAS

In [8]:
only_crops_df_2002 = spark.sql("SELECT {} FROM df_2002 WHERE SECTOR_DESC='CROPS'".format(interesting_column_str))
only_crops_df_2002.createOrReplaceTempView("only_crops_df_2002")
only_crops_df_2002.limit(100).toPandas().head(100)

NameError: name 'interesting_column_str' is not defined

In [60]:
check_almonds_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE 'ALMONDS' \
".format(interesting_columns_fewer_coulumns_str))
check_almonds_COMMOD_DESC_2002_df.createOrReplaceTempView("check_almonds_COMMOD_DESC_2002_df")
check_almonds_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC COMMODITY_DESC           STATISTICCAT_DESC   UNIT_DESC  \
0    FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
1    FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
2    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
3    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
4    FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
5    FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
6    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
7    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
8    FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
9    FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
10   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
11   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
12   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
13   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
14   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
15   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
16   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
17   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
18   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
19   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
20   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
21   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
22   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
23   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
24   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
25   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
26   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
27   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
28   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
29   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
30   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
31   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
32   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
33   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
34   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
35   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
36   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
37   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
38   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
39   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
40   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
41   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
42   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
43   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
44   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
45   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
46   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
47   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
48   FRUIT & TREE NUTS        ALMONDS  AREA

In [ ]:
check_other_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%OTHER%'\
".format(interesting_column_str))
check_other_COMMOD_DESC_2002_df.createOrReplaceTempView("check_other_COMMOD_DESC_2002_df")
check_other_COMMOD_DESC_2002_df.toPandas().tail(10000)

In [10]:
check_woody_COMMOD_DESC_2002_df = spark.sql("SELECT {} FROM only_crops_2002_df \
    WHERE COMMODITY_DESC LIKE '%CHRISTMAS TREES%' OR COMMODITY_DESC LIKE '%WOODY%' \
    AND STATISTICCAT_DESC NOT LIKE 'SALES'\
".format(interesting_columns_fewer_coulumns_str))
check_woody_COMMOD_DESC_2002_df.createOrReplaceTempView("check_woody_COMMOD_DESC_2002_df")
check_woody_COMMOD_DESC_2002_df.limit(1000).toPandas().tail(1000)

GROUP_DESC                                COMMODITY_DESC  \
0    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
1    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
2    HORTICULTURE                        SHORT TERM WOODY CROPS   
3    HORTICULTURE                        SHORT TERM WOODY CROPS   
4    HORTICULTURE                        SHORT TERM WOODY CROPS   
5    HORTICULTURE                        SHORT TERM WOODY CROPS   
6    HORTICULTURE                           CUT CHRISTMAS TREES   
7    HORTICULTURE                           CUT CHRISTMAS TREES   
8    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
9    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
10   HORTICULTURE                           CUT CHRISTMAS TREES   
11   HORTICULTURE                           CUT CHRISTMAS TREES   
12   HORTICULTURE                           CUT CHRISTMAS TREES   
13   HORTICULTURE                           CUT CHRISTMAS TREES   
14   HORTICULTURE                        SHORT TERM WOODY CROPS   
15   HORTICULTURE                        SHORT TERM WOODY CROPS   
16   HORTICULTURE                           CUT CHRISTMAS TREES   
17   HORTICULTURE                           CUT CHRISTMAS TREES   
18   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
19   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
20   HORTICULTURE                        SHORT TERM WOODY CROPS   
21   HORTICULTURE                        SHORT TERM WOODY CROPS   
22   HORTICULTURE                        SHORT TERM WOODY CROPS   
23   HORTICULTURE                        SHORT TERM WOODY CROPS   
24   HORTICULTURE                           CUT CHRISTMAS TREES   
25   HORTICULTURE                           CUT CHRISTMAS TREES   
26   HORTICULTURE                        SHORT TERM WOODY CROPS   
27   HORTICULTURE                        SHORT TERM WOODY CROPS   
28   HORTICULTURE                           CUT CHRISTMAS TREES   
29   HORTICULTURE                           CUT CHRISTMAS TREES   
30   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
31   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
32   HORTICULTURE                        SHORT TERM WOODY CROPS   
33   HORTICULTURE                        SHORT TERM WOODY CROPS   
34   HORTICULTURE                           CUT CHRISTMAS TREES   
35   HORTICULTURE                           CUT CHRISTMAS TREES   
36   HORTICULTURE                           CUT CHRISTMAS TREES   
37   HORTICULTURE                           CUT CHRISTMAS TREES   
38   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
39   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
40   HORTICULTURE                        SHORT TERM WOODY CROPS   
41   HORTICULTURE                        SHORT TERM WOODY CROPS   
42   HORTICULTURE                        SHORT TERM WOODY CROPS   
43   HORTICULTURE                        SHORT TERM WOODY CROPS   
44   HORTICULTURE                           CUT CHRISTMAS TREES   
45   HORTICULTURE                           CUT CHRISTMAS TREES   
46   HORTICULTURE                           CUT CHRISTMAS TREES   
47   HORTICULTURE                           CUT CHRISTMAS TREES   
48   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
49   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
50   HORTICULTURE                           CUT CHRISTMAS TREES   
51   HORTICULTURE                           CUT CHRISTMAS TREES   
52   HORTICULTURE                           CUT CHRISTMAS TREES   
53   HORTICULTURE                           CUT CHRISTMAS TREES   
54   HORTICULTURE                        SHORT TERM WOODY CROPS   
55   HORTICULTURE                        SHORT TERM WOODY CROPS   
56   HORTICULTURE                           CUT CHRISTMAS TREES   
57   HORTICULTURE                           CUT CHRISTMAS TREES   
58   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WO

In [14]:
check_hay_COMMOD_DESC_2002_df = spark.sql("SELECT * FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%HAY%'")
check_hay_COMMOD_DESC_2002_df.createOrReplaceTempView("check_hay_COMMOD_DESC_2002_df")
check_hay_COMMOD_DESC_2002_df.limit(100).toPandas().head(100)

GROUP_DESC COMMODITY_DESC                          CLASS_DESC  \
0   FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
1   FIELD CROPS            HAY                         ALL CLASSES   
2   FIELD CROPS            HAY                         ALL CLASSES   
3   FIELD CROPS            HAY                         ALL CLASSES   
4   FIELD CROPS            HAY                             ALFALFA   
5   FIELD CROPS            HAY                             ALFALFA   
6   FIELD CROPS            HAY                             ALFALFA   
7   FIELD CROPS            HAY                         SMALL GRAIN   
8   FIELD CROPS            HAY                         SMALL GRAIN   
9   FIELD CROPS            HAY                                WILD   
10  FIELD CROPS            HAY                                WILD   
11  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
12  FIELD CROPS        HAYLAGE                         ALL CLASSES   
13  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
14  FIELD CROPS        HAYLAGE                         ALL CLASSES   
15  FIELD CROPS            HAY                         ALL CLASSES   
16  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
17  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
18  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
19  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
20  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
21  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
22  FIELD CROPS        HAYLAGE                         ALL CLASSES   
23  FIELD CROPS            HAY                         ALL CLASSES   
24  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
25  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
26  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
27  FIELD CROPS            HAY                             ALFALFA   
28  FIELD CROPS            HAY                             ALFALFA   
29  FIELD CROPS            HAY                         SMALL GRAIN   
30  FIELD CROPS            HAY                         SMALL GRAIN   
31  FIELD CROPS            HAY                         SMALL GRAIN   
32  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
33  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
34  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
35  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
36  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
37  FIELD CROPS            HAY                                WILD   
38  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
39  FIELD CROPS            HAY                         ALL CLASSES   
40  FIELD CROPS            HAY                         ALL CLASSES   
41  FIELD CROPS            HAY                         ALL CLASSES   
42  FIELD CROPS            HAY                             ALFALFA   
43  FIELD CROPS            HAY                             ALFALFA   
44  FIELD CROPS            HAY                         SMALL GRAIN   
45  FIELD CROPS            HAY                         SMALL GRAIN   
46  FIELD CROPS            HAY                                WILD   
47  FIELD CROPS            HAY                                WILD   
48  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
49  FIELD CROPS        HAYLAGE                         ALL CLASSES   
50  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
51  FIELD CROPS        HAYLAGE                         ALL CLASSES   
52  FIELD CROPS            HAY                         ALL CLASSES   
53  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
54  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
55  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
56  FIELD CROPS

In [5]:
check_hay_again_COMMOD_DESC_2002_df = spark.sql("\
        SELECT {} FROM df_2002 WHERE COMMODITY_DESC LIKE 'HAY & HAYLAGE' AND (UNIT_DESC LIKE 'OPERATIONS' \
        OR UNIT_DESC LIKE 'SQ FT' OR UNIT_DESC LIKE 'ACRES') AND PRODN_PRACTICE_DESC = 'ALL PRODUCTION PRACTICES' \
".format(interesting_column_str))
check_hay_again_COMMOD_DESC_2002_df.createOrReplaceTempView("check_hay_again_COMMOD_DESC_2002_df")
check_hay_again_COMMOD_DESC_2002_df.limit(6).toPandas().head(10000)

GROUP_DESC COMMODITY_DESC   CLASS_DESC       PRODN_PRACTICE_DESC  \
0  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
1  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
2  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
3  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
4  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
5  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   

          UTIL_PRACTICE_DESC STATISTICCAT_DESC   UNIT_DESC  \
0  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
1  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
2  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
3  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
4  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
5  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   

                                       SHORT_DESC  \
0                 HAY & HAYLAGE - ACRES HARVESTED   
1  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
2  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
3  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
4  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
5  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   

                       LOCATION_DESC     DOMAIN_DESC   VALUE  
0  ALABAMA, NORTHERN VALLEY, COLBERT           TOTAL  12,055  
1  ALABAMA, NORTHERN VALLEY, COLBERT           TOTAL     287  
2  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED     122  
3  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED      26  
4  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED     137  
5  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED       2

In [56]:
check_cotton_COMMOD_DESC_2002_df = spark.sql("SELECT * FROM df_2002 WHERE COMMODITY_DESC LIKE '%COTTON%'")
check_cotton_COMMOD_DESC_2002_df.createOrReplaceTempView("check_cotton_COMMOD_DESC_2002_df")
check_cotton_COMMOD_DESC_2002_df.limit(6).toPandas().head(6)

SOURCE_DESC SECTOR_DESC   GROUP_DESC COMMODITY_DESC   CLASS_DESC  \
0      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
1      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
2      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
3      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
4      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
5      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   

        PRODN_PRACTICE_DESC         UTIL_PRACTICE_DESC STATISTICCAT_DESC  \
0  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
1  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
2                 IRRIGATED  ALL UTILIZATION PRACTICES    AREA HARVESTED   
3  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
4  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
5  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   

    UNIT_DESC                                   SHORT_DESC     DOMAIN_DESC  \
0       ACRES                     COTTON - ACRES HARVESTED           TOTAL   
1       ACRES             COTTON, UPLAND - ACRES HARVESTED           TOTAL   
2       ACRES  COTTON, UPLAND, IRRIGATED - ACRES HARVESTED           TOTAL   
3  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED           TOTAL   
4  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED  AREA HARVESTED   
5  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED  AREA HARVESTED   

                        DOMAINCAT_DESC AGG_LEVEL_DESC  STATE_ANSI  \
0                        NOT SPECIFIED         COUNTY         1.0   
1                        NOT SPECIFIED         COUNTY         1.0   
2                        NOT SPECIFIED         COUNTY         1.0   
3                        NOT SPECIFIED         COUNTY         1.0   
4  AREA HARVESTED: (1.0 TO 24.9 ACRES)         COUNTY         1.0   
5   AREA HARVESTED: (100 TO 249 ACRES)         COUNTY         1.0   

   STATE_FIPS_CODE STATE_ALPHA STATE_NAME  ASD_CODE         ASD_DESC  \
0              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
1              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
2              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
3              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
4              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
5              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   

   COUNTY_ANSI  COUNTY_CODE COUNTY_NAME REGION_DESC ZIP_5  WATERSHED_CODE  \
0         33.0         33.0     COLBERT        None  None             0.0   
1         33.0         33.0     COLBERT        None  None             0.0   
2         33.0         33.0     COLBERT        None  None             0.0   
3         33.0         33.0     COLBERT        None  None             0.0   
4         33.0         33.0     COLBERT        None  None             0.0   
5         33.0         33.0     COLBERT        None  None             0.0   

  WATERSHED_DESC CONGR_DISTRICT_CODE  COUNTRY_CODE   COUNTRY_NAME  \
0           None                None        9000.0  UNITED STATES   
1           None                None        9000.0  UNITED STATES   
2           None                None        9000.0  UNITED STATES   
3           None                None        9000.0  UNITED STATES   
4           None                None        9000.0  UNITED STATES   
5           None                None        9000.0  UNITED STATES   

                       LOCATION_DESC    YEAR FREQ_DESC  BEGIN_CODE  END_CODE  \
0  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
1  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
2  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
3  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
4  ALABAMA, NORTHE

In [11]:
check_tubers_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%TUBERS%' OR COMMODITY_DESC LIKE 'TARO' \
".format(interesting_columns_fewer_coulumns_str))
check_tubers_COMMOD_DESC_2002_df.createOrReplaceTempView("check_tubers_COMMOD_DESC_2002_df")
check_tubers_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC                     COMMODITY_DESC   STATISTICCAT_DESC  \
0     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
1     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
2     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
3     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
4     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
5     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
6     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
7     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
8     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
9     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
10    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
11    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
12    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
13    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
14    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
15    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
16    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
17    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
18    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
19    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
20    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
21    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
22    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
23    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
24    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
25    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
26    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
27    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
28    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
29    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
30    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
31    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
32    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
33    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
34    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
35    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
36    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
37    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
38    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
39    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
40    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
41    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
42    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
43    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
44    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
45    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
46    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
47    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
48    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
49    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
50    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
51  

In [1]:
check_ginger_corms_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%TUBERS%' OR COMMODITY_DESC LIKE 'GINGER ROOT' \
".format(interesting_columns_fewer_coulumns_str))
check_ginger_corms_COMMOD_DESC_2002_df.createOrReplaceTempView("check_ginger_corms_COMMOD_DESC_2002_df")
check_ginger_corms_COMMOD_DESC_2002_df.toPandas().head(10000)

NameError: name 'spark' is not defined

In [7]:
distinct_statisticcat_df = spark.sql('select distinct STATISTICCAT_DESC from only_crops_2002_df')
distinct_statisticcat_df.show(250, False)

+--------------------------+
|STATISTICCAT_DESC         |
+--------------------------+
|PRODUCTION                |
|TAPS                      |
|AREA BEARING              |
|SALES                     |
|AREA NON-BEARING          |
|AREA IN PRODUCTION        |
|AREA GROWN                |
|CAPACITY                  |
|YIELD                     |
|AREA HARVESTED            |
|AREA BEARING & NON-BEARING|
|AREA NOT HARVESTED        |
+--------------------------+



In [15]:
distinct_commodity_df = spark.sql("SELECT DISTINCT COMMODITY_DESC FROM only_crops_2002_df")
#distinct_commodity_df.take(50)
distinct_commodity_df.show(250, False)                                 

+--------------------------------------------+
|COMMODITY_DESC                              |
+--------------------------------------------+
|TANGELOS                                    |
|OATS                                        |
|TEMPLES                                     |
|PEAS                                        |
|PASSION FRUIT                               |
|CRAMBE                                      |
|SORGHUM                                     |
|RYE                                         |
|AMARANTH                                    |
|FIELD CROPS, OTHER                          |
|TARO                                        |
|TANGERINES                                  |
|ARTICHOKES                                  |
|PAPAYAS                                     |
|CUCUMBERS                                   |
|BOYSENBERRIES                               |
|POMEGRANATES                                |
|PEACHES                                     |
|CARROTS     

In [10]:
test_df = spark.read.parquet('./census_truncated.parquet')
test_df.createOrReplaceTempView('test_df')

In [13]:
test_df.limit(2).toPandas().head()
test_df.describe
#test_df['STATE_FIPS_CODE'] = test_df['STATE_FIPS_CODE'].str.

<bound method DataFrame.describe of DataFrame[SOURCE_DESC: string, SECTOR_DESC: string, GROUP_DESC: string, COMMODITY_DESC: string, CLASS_DESC: string, PRODN_PRACTICE_DESC: string, UTIL_PRACTICE_DESC: string, STATISTICCAT_DESC: string, UNIT_DESC: string, SHORT_DESC: string, DOMAIN_DESC: string, DOMAINCAT_DESC: string, AGG_LEVEL_DESC: string, STATE_ANSI: bigint, STATE_FIPS_CODE: bigint, STATE_ALPHA: string, STATE_NAME: string, ASD_CODE: bigint, ASD_DESC: string, COUNTY_ANSI: bigint, COUNTY_CODE: bigint, COUNTY_NAME: string, REGION_DESC: double, ZIP_5: double, WATERSHED_CODE: bigint, WATERSHED_DESC: double, CONGR_DISTRICT_CODE: double, COUNTRY_CODE: bigint, COUNTRY_NAME: string, LOCATION_DESC: string, YEAR: bigint, FREQ_DESC: string, BEGIN_CODE: bigint, END_CODE: bigint, REFERENCE_PERIOD_DESC: string, WEEK_ENDING: double, LOAD_TIME: string, VALUE: string, CV_%: double, __index_level_0__: bigint]>

In [14]:
cleaned_2002_df.describe

<bound method DataFrame.describe of DataFrame[CLASS_DESC: string, COMMODITY_DESC: string, SHORT_DESC: string, UNIT_DESC: string, VALUE: string, YEAR: double, COUNTY_NAME: string, COUNTY_CODE: double, ASD_DESC: string, STATE_ALPHA: string, STATISTICCAT_DESC: string]>